In [1]:
import pandas as pd
import numpy as np
import time
import os
from collections import deque
from requests.exceptions import HTTPError
import requests
from datetime import datetime

from stem import Signal
from stem.control import Controller
import socks
import socket

In [2]:
path = 'E:/Dataset/ransomware/BitcoinHeistData.csv'
df = pd.read_csv(path)

In [3]:
df = df.drop_duplicates(subset='address')

In [4]:
df

address  year  day  length    weight  \
0         111K8kZAEnJg245r2cM6y9zgJGHZtJPy6  2017   11      18  0.008333   
1        1123pJv8jzeFQaCV4w644pzQJzVWay2zcA  2016  132      44  0.000244   
2        112536im7hy6wtKbpH1qYDWtTyMRAcA2p7  2016  246       0  1.000000   
3        1126eDRw2wqSkWosjTCre8cjjQW8sSeWH7  2016  322      72  0.003906   
4        1129TSjKtx65E35GiUo4AYVeyo48twbrGX  2016  238     144  0.072848   
...                                     ...   ...  ...     ...       ...   
2916691  3CnqtutaKhQT7e7CfBYTeeuHbuQBfTc7JN  2018  330     144  5.763587   
2916692  12D3trgho1vJ4mGtWBRPyHdMJK96TRYSry  2018  330       0  0.111111   
2916693  1P7PputTcVkhXBmXBvSD9MJ3UYPsiou1u2  2018  330       0  1.000000   
2916695  15iPUJsRNZQZHmZZVwmQ63srsmughCXV4a  2018  330       0  0.500000   
2916696  3LFFBxp15h9KSFtaw55np8eP5fv6kdK17e  2018  330     144  0.073972   

         count  looped  neighbors        income            label  
0            1       0          2  1.000500e+08  princetonCerber  
1            1       0          1  1.000000e+08   princetonLocky  
2            1       0          2  2.000000e+08  princetonCerber  
3            1       0          2  7.120000e+07  princetonCerber  
4          456       0          1  2.000000e+08   princetonLocky  
...        ...     ...        ...           ...              ...  
2916691   6237       0          2  1.949961e+09            white  
2916692      1       0          1  1.255809e+09            white  
2916693      1       0          1  4.409699e+07            white  
2916695      1       0          1  1.780427e+08            white  
2916696   6800       0          2  1.123500e+08            white  

[2631095 rows x 10 columns]

In [8]:
sample = df[(df['year'] > 2015) & ((df['label']) == 'white')].sample(n=300, random_state=42)

In [12]:
sample['address'].to_csv('legit_addresses.csv', index=False)

In [12]:
df.value_counts('label')

label
white                          2610246
princetonCerber                   9177
princetonLocky                    6584
paduaCryptoWall                   1894
montrealCryptoLocker              1509
montrealCryptXXX                  1354
montrealDMALockerv3                143
montrealSamSam                      44
montrealCryptoTorLocker2015         32
montrealNoobCrypt                   28
montrealDMALocker                   21
paduaKeRanger                       10
montrealFlyper                       8
montrealGlobe                        7
montrealCryptConsole                 5
montrealWannaCry                     5
montrealGlobev3                      5
montrealEDA2                         4
montrealXLockerv5.0                  3
montrealXTPLocker                    3
montrealJigSaw                       3
paduaJigsaw                          2
montrealAPT                          2
montrealSam                          1
montrealRazy                         1
montrealVenusLocker

GET /address/:address/txs

https://btcscan.org/api/

In [18]:
import requests
address = "1HqcdC83mPWV5B5Y4KSqQFH6ec7eQn6LwV"
url = f"https://btcscan.org/api/address/{address}/txs"

response = requests.get(url)

# Controlla se la richiesta ha avuto successo
if response.status_code == 200:
    data = response.json()  # Supponendo che l'API restituisca JSON
    data
else:
    print(f"Errore nella richiesta: {response.status_code}")

https://btcscan.org/address/1123pJv8jzeFQaCV4w644pzQJzVWay2zcA

In [19]:
data

[]

In [21]:
df.value_counts('address')

address
1111111111111111111114oLvT2           1
1JsKEwpJ6UnZcrAMDnEEzcNtWPhHwjyP6t    1
1JsHNGc64BMQ6vn24v4Wh2GeRbMX6bKv3g    1
1JsHNdqEmtNGWN8iMkMGYjZ2xJUseQBeb2    1
1JsHPaxwKNVBLfobqtfh47q5Dp4UU31V8u    1
                                     ..
1AQqxQt4x15iLkRMvcdi9BAtgc3HoSUJcz    1
1AQr2WWqfkTbCEvdwJSGyLJzJw36emU4He    1
1AQr5BDFvN361EdH8xeUPcJA1xgzf822XW    1
1AQr5BEhNSQrZeWFazvZ2tkFb7edrwiX5L    1
unknown                               1
Name: count, Length: 2631095, dtype: int64

In [22]:
df[df['address'] == '1111111111111111111114oLvT2']

address  year  day  length  weight  count  looped  \
565845  1111111111111111111114oLvT2  2012  170       0     1.0      1       0   

        neighbors       income  label  
565845          1  200200000.0  white

# Ransomware complete

## Graph structure

Node: [address, depth, label]
- label: family/white

Edge: add1 --[timestamp, scriptpubkey_type, tot_value, sender_value, #reused_address]--> add2

In [3]:
def to_btc(n):
    formatted_n = n / 100000000
    return formatted_n

In [6]:
def recognize_script(tokens):
        if len(tokens) == 5 and tokens[0] == "76" and tokens[1] == "a9" and tokens[3] == "88" and tokens[4] == "ac":
            return "P2PKH"
        elif len(tokens) == 3 and tokens[0] == "a9" and tokens[2] == "87":
            return "P2SH"
        elif len(tokens) == 2 and tokens[0] == "00" and len(tokens[1]) == 40:  
            return "P2WPKH"
        elif len(tokens) == 2 and tokens[0] == "00" and len(tokens[1]) == 64: 
            return "P2WSH"
        else:
            return "Unknown"
            
def parse_script(script_hex):
    OPCODES = {
        "76": "OP_DUP",
        "a9": "OP_HASH160",
        "88": "OP_EQUALVERIFY",
        "ac": "OP_CHECKSIG",
        "00": "OP_0",
    }

    i = 0
    tokens = []
    while i < len(script_hex):
        opcode = script_hex[i:i+2]
        if opcode in OPCODES:
            tokens.append(opcode)  # Opcode
            i += 2
        else:
            data_length = int(opcode, 16)
            data = script_hex[i+2:i+2+data_length*2]
            tokens.append(data)
            i += 2 + data_length * 2


    script_type = recognize_script(tokens)
    return script_type

In [3]:
path = 'E:/Dataset/ransomware/ransomware_dataset_04_11_2018/dataset/blockchain' 
file_h = 'expanded_addresses_stats_headers.csv'
file = 'expanded_addresses_stats.csv'
headers = pd.read_csv(f"{path}/{file_h}").columns
exp = pd.read_csv(f"{path}/{file}", names=headers)

In [3]:
exp['family'].value_counts()

family
Locky                  7094
CryptXXX               1742
CryptoLocker            968
DMALockerv3             165
CryptoTorLocker2015     159
Globe                    87
SamSam                   47
EDA2                     33
NoobCrypt                28
Flyper                   26
Globev3                  19
JigSaw                   17
Cryptohitman             14
TowerWeb                 14
CryptConsole              7
WannaCry                  6
VenusLocker               5
XTPLocker                 4
XLockerv5.0               3
APT                       2
ComradeCircle             1
CTB-Locker                1
7ev3n                     1
CryptoHost                1
Chimera                   1
NullByte                  1
TeslaCrypt                1
Phoenix                   1
NotPetya                  1
Xorist                    1
Razy                      1
Exotic                    1
GlobeImposter             1
Sam                       1
XLocker                   1
DMALocker    

## Start tor (cmd)
- tor.exe -f "C:\Users\alema\Desktop\Tor Browser\Browser\TorBrowser\Data\Tor\torrc"

In [1]:
controller = Controller.from_port(port=9051)

def connectTor():
    socks.setdefaultproxy(socks.PROXY_TYPE_SOCKS5, "127.0.0.1", 9050, True)
    socket.socket = socks.socksocket

def renewTor():
    controller.authenticate("your_password")
    controller.signal(Signal.NEWNYM)

NameError: name 'Controller' is not defined

In [9]:
#EXTRACT A STACK OF OUTGOING TXs
def get_explorer_data(address): #SEEDS
    retries = 0
    delay = 10
    url = f"https://blockchain.info/rawaddr/{address}" 
    
    out_txs = []
    while True:#retries < 5:
        try:
            renewTor()
            connectTor()
            time.sleep(10)
            response = requests.get(url)
            response.raise_for_status()
            data = response.json()
            break
        except HTTPError as http_err:
            if response.status_code == 429:  # Too Many Requests
                time.sleep(delay) 
                retries += 1
                #print(f"{http_err}")
            else:
                print(f"HTTP error occurred: {http_err}")
                time.sleep(1)
                retries += 1
        except Exception as err:
            print(f"Generic error: {err}")
            time.sleep(1)
            retries += 1
    
    #Filter only outgoing txs
    c_in_txs = 0
    for tx in data['txs']:
        if tx['result'] < 0:
            out_txs += [tx]
        else:
            c_in_txs += 1
    data['txs'] = out_txs
    
    return data, c_in_txs

In [10]:
#GET LAST 250 OUTGOING TXs
def get_last_txs(address):
    n = 250
    data, c_in_tx = get_explorer_data(address)
    offset = 0
    while((len(data['txs']) + c_in_tx) < data['n_tx']) and (len(data['txs']) < n) :
        offset = len(data['txs']) + c_in_tx
        tmp, tmp_c_in_tx = get_explorer_data(f"{address}?&offset={offset}&limit={abs(len(data['txs']) - n)}")
        c_in_tx += tmp_c_in_tx
        data['txs'] = data['txs'] + tmp['txs']
    data['txs'].reverse()
    return data['txs']

In [11]:
#ISOLATE LAST n OUTGOING TXs AFTER SPECIFIED TIME
#address: neighbors
def filter_txs(address, start_time):
    data, _ = get_explorer_data(address)
    if len(data['txs']) > 0:
        if data['txs'][(len(data['txs'])-1)]['time'] <= start_time:
            while (data['txs'][(len(data['txs'])-1)]['time'] > start_time):
                #time.sleep(10)
                offset = len(data['txs'])
                print(f"{data['txs'][(len(data['txs'])-1)]['time']} VS {start_time}")
                tmp, _ = get_explorer_data(f"{address}?&offset={offset}")
                data['txs'] = data['txs'] + tmp['txs']
        
        i = len(data['txs'])-1
        while data['txs'][i]['time'] < start_time:
            if i == 0:
                return []
            i -= 1
        del data['txs'][i+1:len(data['txs'])]
        data['txs'].reverse() #Least recent first
        if len(data['txs'])>50:
            del data['txs'][50:len(data['txs'])]
        return data
    return []

In [12]:
# A QUESTO PUNTO LE TRANSAZIONI SONO GIà FILTRATE - SOLO OUTGOING TXS e DOPO TIMESTAMP

#address: sender address
def build_block(data, address):
    for tx in data['txs']:
        
        fee = to_btc(tx['fee'])
        txid = tx['hash']
        timestamp = tx['time']

        addr_ins = []
        val_ins = []
        addr_outs = []
        val_outs =  []
        scripts = []

        addr_uses = 0
        tot_value = 0
        sender_value = 0

        ins = tx['inputs']
        for el in ins:
            try:
                addr = el['prev_out']['addr']
            except KeyError as ke:
                addr = 'Unknown'
                #print('Unknown address among outputs')
            addr_ins.append(addr)
            val_ins.append(to_btc(el['prev_out']['value']))
            
        out = tx['out']
        for el in out:
            try:
                addr = el['addr'] 
            except KeyError as ke:
                addr = 'Unknown'
                #print('Unknown address among outputs')
            addr_outs.append(addr)
            value = to_btc(el['value']) 
            val_outs.append(value)
            script_type = parse_script(el['script']) 
            scripts.append(script_type)
                    
        yield pd.DataFrame([{
                'txid': txid,
                'src': addr_ins,
                'values_in': val_ins,
                'dst': addr_outs,
                'values_out': val_outs,
                'scripts': scripts,
                'fee': fee,
                'timestamp': datetime.fromtimestamp(timestamp) #timestamp
                }]), addr_outs, timestamp


In [13]:
# Genera grafo .csv a relativo a indirizzo 'address' 
def get_tx_graph(address):
    transactions = pd.DataFrame(columns = ['seed', 'txid', 'src', 'values_in', 'dst', 'values_out', 'scripts', 'fee', 'timestamp']) 
    coda = deque()
    txs = get_last_txs(address)
    for t, _, _ in build_block(txs):
        t['seed'] = address
        transactions = pd.concat([t, transactions], ignore_index = True)
        
    for tx in txs:
        timestamp = tx['time']
        for out in tx['out']:
            coda.append((out['addr'], timestamp, 1))

    d = 4 #Max_depth
    visited = dict()
    
    while coda:
        el = coda.popleft()
        addr = el[0]
        timestamp = el[1]
        depth = el[2]
        
        #print(f"Exploring {addr} at depth {depth} after {timestamp}")
        if (addr not in visited) and (addr != 'Unknown'):
            visited[addr] = depth
            if depth < d:
                depth += 1
                data = filter_txs(addr, timestamp) 
                if len(data) != 0:
                    #print(f"Processing {addr}")
                    print(f"Processing {addr} at time {datetime.fromtimestamp(timestamp)}")
                    for tx, neighbors, timestamp in build_block(data, addr):
                        for n in neighbors:
                            if (n not in visited) and (depth < d):
                                coda.append((n, timestamp, depth))
                        tx['seed'] = addr
                        transactions = pd.concat([transactions, tx], ignore_index = True)
                    #print(len(transactions))
    transactions.to_csv(f"D:/Tesi/Graphs/{address}.csv")

In [14]:
from queue import Queue
seeds = Queue()
for seed in exp['address']:
    seeds.put(seed)

In [ ]:
#3 threads
import threading

def process_seed():
    while True:
        try:
            seed = seeds.get(timeout = 1) 
        except queue.Empty:
            break
        time.sleep(1)
        get_tx_graph(seed)
        seeds.task_done()


threads = []
for i in range(3):  # 3 thread in esecuzione
    t = threading.Thread(target=process_seed, name=f"Thread-{i+1}")
    threads.append(t)
    t.start()

# Aspetta che tutti i thread completino il lavoro
for t in threads:
    t.join()

Generic error: unable to use the control socket
Processing 1EuSL6KEqt3QovuRXpeQcghNNqv7ioaypE at time 2016-05-10 08:50:07
Processing 1AEoiHY23fbBn8QiJ5y6oAjrhRY1Fb85uc at time 2013-11-11 08:42:39
Processing 15ZQDGkALnkFykbnt8HAnpBYLciEenHH2g at time 2016-06-11 08:18:09
Processing 17Ugh96JsKDKKsf53JCTCZejFmZKmjfnfx at time 2016-05-10 08:50:07
Processing 1JCzaqBQPKNEzqkZ9Bg1ffRyrgpUee8QDo at time 2013-11-11 08:42:39
Processing 12hZPN3TkcB9Js6UCYgFZjf5L352VfzCXN at time 2016-06-11 08:18:09
Processing 1GZKujBRtN7YV5T3JgcinnnM6aGqraCLz4 at time 2016-05-10 10:28:31
Processing 1HpPqL1jaeUJTSUHKiKGvXCtPt6KNjhBSJ at time 2016-06-11 08:23:58
Processing 19Ynm8s4pYQ1WDWNVDJFNi89RZStju2YZw at time 2013-11-11 09:43:31
Processing 1TPQwhRPd7AfmVhf2ZqnW62cDYZg5196J at time 2016-05-10 10:28:31
Processing 1L1yEN2e9ukecZKVNYh94DYcyD3YfbP4iU at time 2013-11-11 09:43:31
Processing 1HFqSHaWwU112zASJyMQ7mzosWLWTbUdoh at time 2016-06-11 08:23:58
Processing 13PNmyEWR3roj5nyojhhfiuZKs95Xw5X6h at time 2016-05-11 